# minTE Quick Start
---

Gehua Tong, May 2022

*Image Acquisition and Reconstruction Group, Columbia Magnetic Resonance Research Center*

---
Using the PyPulseq library, this notebook quickly generates, displays, and saves minTE sequences that can be then downloaded for scanners set up with Pulseq interpreters.

We will make five sequences: 
1. 2D UTE using half pulses 
2. 2D UTE using full pulses
3. 3D UTE using half pulses
4. 3D UTE using full pulses
5. 3D CODE

Run each section to generate a display the sequence. Small matrix sizes were chosen for speed and ease of display. Please adjust the parameters and display time ranges as you see fit.

Units:
* All timings are in [seconds]
* All locations and sizes are in [meters]
* Flip angles are in [degrees]
* `ro_asymmetry` is the ratio of unacquired / acquired k-space line length for each line that extends from -$k_{max}$ to $k_{max}$ at its own angle, which ranges from 0 to 2π 

Refer to the documentation for more details.

## Install minTE 

In [1]:
!pip install git+https://github.com/imr-framework/minTE.git@e91d9cc141f2be07e2e794157f77633121ee8ac8

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/imr-framework/minTE.git (to revision e91d9cc141f2be07e2e794157f77633121ee8ac8) to /tmp/pip-req-build-7459o7zn
  Running command git clone -q https://github.com/imr-framework/minTE.git /tmp/pip-req-build-7459o7zn
  Running command git rev-parse -q --verify 'sha^e91d9cc141f2be07e2e794157f77633121ee8ac8'
  Running command git fetch -q https://github.com/imr-framework/minTE.git e91d9cc141f2be07e2e794157f77633121ee8ac8
  Running command git checkout -q e91d9cc141f2be07e2e794157f77633121ee8ac8
     |████████████████████████████████| 27.4 MB 1.5 MB/s 
     |████████████████████████████████| 15.3 MB 75.1 MB/s 
     |████████████████████████████████| 10.3 MB 60.5 MB/s 
     |████████████████████████████████| 821 kB 63.1 MB/s 
     |████████████████████████████████| 105 kB 67.1 MB/s 
  Created wheel for minTE: filename=minTE-0.0.2-py3-none-any.whl size=5905353 sha256=7e

## Install plotly for sequence display

In [2]:
!pip install plotly==5.7.0

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 28.8 MB 85.7 MB/s 
  Attempting uninstall: plotly
    Found existing installation: plotly 5.5.0
    Uninstalling plotly-5.5.0:
      Successfully uninstalled plotly-5.5.0


## Import functions



In [3]:
from minTE.sequences.write_UTE_2D import *
from minTE.sequences.write_UTE_3D import *
from minTE.sequences.write_CODE import *
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from google.colab import files 
import numpy as np 
from pypulseq.Sequence.sequence import Sequence 
import math


## Define display functions

In [4]:
def export_waveforms(seq, time_range=(0, np.inf)):
    """
    Plot `Sequence`.
    Parameters
    ----------
    time_range : iterable, default=(0, np.inf)
        Time range (x-axis limits) for all waveforms. Default is 0 to infinity (entire sequence).
    Returns
    -------
    all_waveforms: dict
        Dictionary containing all sequence waveforms and time array(s)
        The keys are listed here:
        't_adc' - ADC timing array [seconds]
        't_rf' - RF timing array [seconds]
        ''
        'adc' - ADC complex signal (amplitude=1, phase=adc phase) [a.u.]
        'rf' - RF complex signal []
        'gx' - x gradient []
        'gy' - y gradient []
        'gz' - z gradient []
    """
    # Check time range validity
    if not all([isinstance(x, (int, float)) for x in time_range]) or len(time_range) != 2:
        raise ValueError('Invalid time range')

    t0 = 0
    adc_t_all = np.array([])
    adc_signal_all = np.array([],dtype=complex)
    rf_t_all =np.array([])
    rf_signal_all = np.array([],dtype=complex)
    rf_t_centers = np.array([])
    rf_signal_centers = np.array([],dtype=complex)
    gx_t_all = np.array([])
    gy_t_all = np.array([])
    gz_t_all = np.array([])
    gx_all = np.array([])
    gy_all = np.array([])
    gz_all = np.array([])


    for block_counter in range(len(seq.dict_block_events)): # For each block
        block = seq.get_block(block_counter + 1)  # Retrieve it
        is_valid = time_range[0] <= t0 <= time_range[1] # Check if "current time" is within requested range.
        if is_valid:
            # Case 1: ADC
            if hasattr(block, 'adc'):
                adc = block.adc # Get adc info
                # From Pulseq: According to the information from Klaus Scheffler and indirectly from Siemens this
                # is the present convention - the samples are shifted by 0.5 dwell # OK

                t = adc.delay + (np.arange(int(adc.num_samples)) + 0.5) * adc.dwell
                adc_t = t0 + t
                adc_signal = np.exp(1j * adc.phase_offset) * np.exp(1j * 2 * np.pi * t * adc.freq_offset)
                adc_t_all = np.append(adc_t_all, adc_t)
                adc_signal_all = np.append(adc_signal_all, adc_signal)

            if hasattr(block, 'rf'):
                rf = block.rf
                tc, ic = calc_rf_center(rf)
                t = rf.t + rf.delay
                tc = tc + rf.delay
                #
                # sp12.plot(t_factor * (t0 + t), np.abs(rf.signal))
                # sp13.plot(t_factor * (t0 + t), np.angle(rf.signal * np.exp(1j * rf.phase_offset)
                #                                         * np.exp(1j * 2 * math.pi * rf.t * rf.freq_offset)),
                #           t_factor * (t0 + tc), np.angle(rf.signal[ic] * np.exp(1j * rf.phase_offset)
                #                                          * np.exp(1j * 2 * math.pi * rf.t[ic] * rf.freq_offset)),
                #           'xb')

                rf_t = t0 + t
                rf = rf.signal * np.exp(1j * rf.phase_offset) \
                                                        * np.exp(1j * 2 * math.pi * rf.t * rf.freq_offset)
                rf_t_all = np.append(rf_t_all, rf_t)
                rf_signal_all = np.append(rf_signal_all, rf)
                rf_t_centers = np.append(rf_t_centers, rf_t[ic])
                rf_signal_centers = np.append(rf_signal_centers, rf[ic])

            grad_channels = ['gx', 'gy', 'gz']
            for x in range(len(grad_channels)): # Check each gradient channel: x, y, and z
                if hasattr(block, grad_channels[x]): # If this channel is on in current block
                    grad = getattr(block, grad_channels[x])
                    if grad.type == 'grad':# Arbitrary gradient option
                        # In place unpacking of grad.t with the starred expression
                        g_t = t0 +  grad.delay + [0, *(grad.t + (grad.t[1] - grad.t[0]) / 2),
                                              grad.t[-1] + grad.t[1] - grad.t[0]]
                        g = 1e-3 * np.array((grad.first, *grad.waveform, grad.last))
                    else: # Trapezoid gradient option
                        g_t = t0 + np.cumsum([0, grad.delay, grad.rise_time, grad.flat_time, grad.fall_time])
                        g = 1e-3 * grad.amplitude * np.array([0, 0, 1, 1, 0])

                    if grad.channel == 'x':
                        gx_t_all = np.append(gx_t_all, g_t)
                        gx_all = np.append(gx_all,g)
                    elif grad.channel == 'y':
                        gy_t_all = np.append(gy_t_all, g_t)
                        gy_all = np.append(gy_all,g)
                    elif grad.channel == 'z':
                        gz_t_all = np.append(gz_t_all, g_t)
                        gz_all = np.append(gz_all,g)


        t0 += seq.arr_block_durations[block_counter] # "Current time" gets updated to end of block just examined

    all_waveforms = {'t_adc': adc_t_all, 't_rf': rf_t_all, 't_rf_centers': rf_t_centers,
                     't_gx': gx_t_all, 't_gy':gy_t_all, 't_gz':gz_t_all,
                     'adc': adc_signal_all, 'rf': rf_signal_all, 'rf_centers': rf_signal_centers,'gx':gx_all, 'gy':gy_all, 'gz':gz_all,
                     'grad_unit': '[kHz/m]', 'rf_unit': '[Hz]', 'time_unit':'[seconds]'}

    return all_waveforms

In [5]:
def display_seq_interactive(all_waveforms,time_range=(0,np.inf)): 
  fig = make_subplots(rows=3, cols=2,
      subplot_titles=("RF magnitude", "Gx", "RF phase", "Gy", "ADC", "Gz"),shared_xaxes='all',row_heights=[10,10,10])

  fig.add_trace(go.Scatter(x=all_waveforms['t_rf'],y=np.absolute(all_waveforms['rf']),mode='lines',name='RF magnitude',line=dict(color='blue',width=2)),
                row=1,col=1)
  fig.add_trace(go.Scatter(x=all_waveforms['t_rf'],y=np.angle(all_waveforms['rf']),mode='lines',name='RF phase',line=dict(color='gray',width=2)),
                row=2,col=1)
  fig.add_trace(go.Scatter(x=all_waveforms['t_adc'],y=np.angle(all_waveforms['adc']),mode='markers',name='ADC with phase',line=dict(color='red',width=2)),
                row=3,col=1)
  fig.add_trace(go.Scatter(x=all_waveforms['t_gx'],y=all_waveforms['gx'],mode='lines',name='Gx',line=dict(color='green', width=2)), 
                row=1,col=2)
  fig.add_trace(go.Scatter(x=all_waveforms['t_gy'],y=all_waveforms['gy'],mode='lines',name='Gy',line=dict(color='orange', width=2)), 
                row=2,col=2)
  fig.add_trace(go.Scatter(x=all_waveforms['t_gz'],y=all_waveforms['gz'],mode='lines',name='Gz',line=dict(color='purple', width=2)), 
                row=3,col=2)
  
  fig.update_xaxes(title_text="Time (seconds)", row=3, col=1,range=time_range)
  fig.update_xaxes(title_text="Time (seconds)", row=3, col=2,range=time_range)
  fig.update_yaxes(title_text=all_waveforms['rf_unit'],row=1,col=1)
  fig.update_yaxes(title_text='[rads]',row=2,col=1)
  fig.update_yaxes(title_text='[rads]',row=3,col=1)
  
  
  fig.show()

In [6]:
def display_ktraj(ktraj,dim):
  fig = go.Figure()
  if dim == 2: 
    fig.add_trace(go.Scatter(x=np.real(ktraj.flatten()),y=np.imag(ktraj.flatten()),marker=dict(size=1,color="red")))

  elif dim == 3:
    fig.add_trace(go.Scatter3d(x=ktraj[:,:,0].flatten(),y=ktraj[:,:,1].flatten(),z=ktraj[:,:,2].flatten(),marker=dict(size=1,color="red")))
  
  fig.update_layout(width=800, height=800, title="K-space trajectory")


  fig.show()

## 2D UTE (full pulse)

In [7]:
seq, TE, ktraj = write_UTE_2D_rf_spoiled(N=64, Nr=202, FOV=253e-3, thk=5e-3, slice_locs=[0],
                                          FA=10, TR=15e-3, ro_asymmetry=0.97, use_half_pulse=False, rf_dur=1e-3,
                                          TE_use=None)
print(seq.test_report())
all_waveforms = export_waveforms(seq, time_range=(0,45e-3)) 
display_seq_interactive(all_waveforms,time_range=(0,45e-3))
display_ktraj(ktraj,2)

TE = 789 us
spoke 1/202 added
spoke 2/202 added
spoke 3/202 added
spoke 4/202 added
spoke 5/202 added
spoke 6/202 added
spoke 7/202 added
spoke 8/202 added
spoke 9/202 added
spoke 10/202 added
spoke 11/202 added
spoke 12/202 added
spoke 13/202 added
spoke 14/202 added
spoke 15/202 added
spoke 16/202 added
spoke 17/202 added
spoke 18/202 added
spoke 19/202 added
spoke 20/202 added
spoke 21/202 added
spoke 22/202 added
spoke 23/202 added
spoke 24/202 added
spoke 25/202 added
spoke 26/202 added
spoke 27/202 added
spoke 28/202 added
spoke 29/202 added
spoke 30/202 added
spoke 31/202 added
spoke 32/202 added
spoke 33/202 added
spoke 34/202 added
spoke 35/202 added
spoke 36/202 added
spoke 37/202 added
spoke 38/202 added
spoke 39/202 added
spoke 40/202 added
spoke 41/202 added
spoke 42/202 added
spoke 43/202 added
spoke 44/202 added
spoke 45/202 added
spoke 46/202 added
spoke 47/202 added
spoke 48/202 added
spoke 49/202 added
spoke 50/202 added
spoke 51/202 added
spoke 52/202 added
spoke 53/

## 2D UTE (half pulse)


In [8]:
seq, TE, ktraj = write_UTE_2D_rf_spoiled(N=64, Nr=202, FOV=253e-3, thk=5e-3, slice_locs=[0],
                                          FA=10, TR=15e-3, ro_asymmetry=0.97, use_half_pulse=True, rf_dur=1e-3,
                                          TE_use=None)
print(seq.test_report())
# Display sequence 
all_waveforms = export_waveforms(seq, time_range=(0,50e-3))
display_seq_interactive(all_waveforms,time_range=(0,50e-3))
# Display kspace 
display_ktraj(ktraj,2)

TE = 419 us
spoke 1/202 added
spoke 2/202 added
spoke 3/202 added
spoke 4/202 added
spoke 5/202 added
spoke 6/202 added
spoke 7/202 added
spoke 8/202 added
spoke 9/202 added
spoke 10/202 added
spoke 11/202 added
spoke 12/202 added
spoke 13/202 added
spoke 14/202 added
spoke 15/202 added
spoke 16/202 added
spoke 17/202 added
spoke 18/202 added
spoke 19/202 added
spoke 20/202 added
spoke 21/202 added
spoke 22/202 added
spoke 23/202 added
spoke 24/202 added
spoke 25/202 added
spoke 26/202 added
spoke 27/202 added
spoke 28/202 added
spoke 29/202 added
spoke 30/202 added
spoke 31/202 added
spoke 32/202 added
spoke 33/202 added
spoke 34/202 added
spoke 35/202 added
spoke 36/202 added
spoke 37/202 added
spoke 38/202 added
spoke 39/202 added
spoke 40/202 added
spoke 41/202 added
spoke 42/202 added
spoke 43/202 added
spoke 44/202 added
spoke 45/202 added
spoke 46/202 added
spoke 47/202 added
spoke 48/202 added
spoke 49/202 added
spoke 50/202 added
spoke 51/202 added
spoke 52/202 added
spoke 53/

## 3D UTE (full pulse) 

In [9]:
seq, TE, ktraj = write_UTE_3D_rf_spoiled(N=16, FOV=250e-3, slab_thk=253e-3, FA=10, TR=15e-3, ro_asymmetry=0.97,
                        os_factor=1, rf_type='sinc', rf_dur=1e-3, use_half_pulse=False, save_seq=True)
print(seq.test_report())
# Display sequence 
all_waveforms = export_waveforms(seq, time_range=(0,45e-3))
display_seq_interactive(all_waveforms,time_range=(0,45e-3))
# Display kspace 
display_ktraj(ktraj,3)

Using 832 spokes, with 26 thetas and 32 phis
TE = 585 us
Spokes: 1/832
Spokes: 2/832
Spokes: 3/832
Spokes: 4/832
Spokes: 5/832
Spokes: 6/832
Spokes: 7/832
Spokes: 8/832
Spokes: 9/832
Spokes: 10/832
Spokes: 11/832
Spokes: 12/832
Spokes: 13/832
Spokes: 14/832
Spokes: 15/832
Spokes: 16/832
Spokes: 17/832
Spokes: 18/832
Spokes: 19/832
Spokes: 20/832
Spokes: 21/832
Spokes: 22/832
Spokes: 23/832
Spokes: 24/832
Spokes: 25/832
Spokes: 26/832
Spokes: 27/832
Spokes: 28/832
Spokes: 29/832
Spokes: 30/832
Spokes: 31/832
Spokes: 32/832
Spokes: 33/832
Spokes: 34/832
Spokes: 35/832
Spokes: 36/832
Spokes: 37/832
Spokes: 38/832
Spokes: 39/832
Spokes: 40/832
Spokes: 41/832
Spokes: 42/832
Spokes: 43/832
Spokes: 44/832
Spokes: 45/832
Spokes: 46/832
Spokes: 47/832
Spokes: 48/832
Spokes: 49/832
Spokes: 50/832
Spokes: 51/832
Spokes: 52/832
Spokes: 53/832
Spokes: 54/832
Spokes: 55/832
Spokes: 56/832
Spokes: 57/832
Spokes: 58/832
Spokes: 59/832
Spokes: 60/832
Spokes: 61/832
Spokes: 62/832
Spokes: 63/832
Spokes:

## 3D UTE (half pulse)

In [10]:
seq, TE, ktraj = write_UTE_3D_rf_spoiled(N=16, FOV=250e-3, slab_thk=253e-3, FA=10, TR=15e-3, ro_asymmetry=0.97,
                        os_factor=1, rf_type='sinc', rf_dur=1e-3, use_half_pulse=True, save_seq=True)
print(seq.test_report())
# Display sequence 
all_waveforms = export_waveforms(seq, time_range=(0,45e-3))
display_seq_interactive(all_waveforms,time_range=(0,45e-3))
# Display kspace 
display_ktraj(ktraj,3)

Using 832 spokes, with 26 thetas and 32 phis
TE = 40 us
Spokes: 1/832
Spokes: 2/832
Spokes: 3/832
Spokes: 4/832
Spokes: 5/832
Spokes: 6/832
Spokes: 7/832
Spokes: 8/832
Spokes: 9/832
Spokes: 10/832
Spokes: 11/832
Spokes: 12/832
Spokes: 13/832
Spokes: 14/832
Spokes: 15/832
Spokes: 16/832
Spokes: 17/832
Spokes: 18/832
Spokes: 19/832
Spokes: 20/832
Spokes: 21/832
Spokes: 22/832
Spokes: 23/832
Spokes: 24/832
Spokes: 25/832
Spokes: 26/832
Spokes: 27/832
Spokes: 28/832
Spokes: 29/832
Spokes: 30/832
Spokes: 31/832
Spokes: 32/832
Spokes: 33/832
Spokes: 34/832
Spokes: 35/832
Spokes: 36/832
Spokes: 37/832
Spokes: 38/832
Spokes: 39/832
Spokes: 40/832
Spokes: 41/832
Spokes: 42/832
Spokes: 43/832
Spokes: 44/832
Spokes: 45/832
Spokes: 46/832
Spokes: 47/832
Spokes: 48/832
Spokes: 49/832
Spokes: 50/832
Spokes: 51/832
Spokes: 52/832
Spokes: 53/832
Spokes: 54/832
Spokes: 55/832
Spokes: 56/832
Spokes: 57/832
Spokes: 58/832
Spokes: 59/832
Spokes: 60/832
Spokes: 61/832
Spokes: 62/832
Spokes: 63/832
Spokes: 

## 3D CODE 

In [11]:
seq, TE, ktraj = make_code_sequence(FOV=253e-3, N=16, TR=15e-3, flip=10, enc_type='3D',
                      os_factor=1, rf_type='gauss',save_seq=False)
seq.write("CODE.seq")
print(seq.test_report())
# Display sequence 
all_waveforms = export_waveforms(seq, time_range=(0,45e-3))
display_seq_interactive(all_waveforms,time_range=(0,45e-3))
# Display kspace 
display_ktraj(ktraj,3)

3D acq.: using 26 thetas and 32 phis - 832 spokes in total.
TE obtained: 0.75 ms
Number of blocks: 3328
Number of events:
RF:    832
Gx:   1664
Gy:   1664
Gz:   1664
ADC:    832
Delay:   1664
Sequence duration: 12.488320 s
TE: 0.000647 s
TR: 0.015010 s
Flip angle: 10.00 deg
Unique k-space positions (aka cols, rows, etc.): 3327 3327 401 
Dimensions: 3
Spatial resolution: 16.22 mm
Spatial resolution: 16.22 mm
Spatial resolution: 16.22 mm
Repetitions/slices/contrasts: 32.0
Non-cartesian/irregular encoding trajectory detected (eg: EPI, spiral, radial, etc.)
Event timing check passed successfully
Max gradient: 158103 158103 158103 Hz/m == 3.71 3.71 3.71 mT/m
Max slew rate: 5270092227 5270092227 5270092227 Hz/m/s == 123.78 123.78 123.78 mT/m/s
Max absolute gradient: 158103 Hz/m == 3.71 mT/m
Max absolute slew rate: 5.27009e+09 Hz/m/s == 123.78 T/m/s
Number of blocks: 3328
Number of events:
RF:    832
Gx:   1664
Gy:   1664
Gz:   1664
ADC:    832
Delay:   1664
Sequence duration: 12.488320 s
TE:

## Downloading the seqs
The .seq files and k-space trajectories as .mat files can be found in the "files" tab on the left of the Google Colab notebook view and downloaded to your local file system.
